In [1]:
cd Prosody2Vec/

/home/dcor/niskhizov/Prosody2Vec


In [2]:
import torch

In [3]:
# import clearml
# clearml.browser_login()

In [4]:
# from clearml import Task
# task = Task.init(project_name="my project", task_name="my task")

In [5]:
from torch import nn
import torch 
import glob
from IPython.display import clear_output, display, Audio
import copy

In [6]:
import torch

In [7]:
import model

In [8]:
# acoustic = torch.hub.load("bshall/acoustic-model:main", "hubert_soft", trust_repo=True).cuda()
# acoustic = model.AcousticModel(discrete=True).cuda()

In [9]:
# data_dir = './Emotion Speech Dataset/'
# data_dir = '/home/dcor/niskhizov/Prosody2Vec/IEMOCAP_full_release/'
data_dir = '/home/dcor/niskhizov/Prosody2Vec/Emotion Speech Dataset/0018/'
# scan recursively for all .wav files in the data_dir
wav_files = glob.glob(data_dir + '/**/*.wav', recursive=True)



In [10]:
embeddings_dir = 'esd_female_018'

In [11]:
# create pytorch dataset that loads pairs of wav a and embeddings from iemocap_embeddings
from torch.utils.data import Dataset, DataLoader
import numpy as np
import os
import pickle
import torchaudio

class IemocapDataset(Dataset):
    def __init__(self, audio_files):
        self.audio_files = []
        self.embeddings_file = []

        for audio_file in audio_files:
            out_file = f"{embeddings_dir}/{audio_file.split('/')[-1].replace('.wav', '.pkl')}"
            if os.path.exists(out_file):                
                self.embeddings_file.append(out_file)
                self.audio_files.append(audio_file)

    def __len__(self):
        return len(self.embeddings_file)
    
    def __getitem__(self, idx):

        wav_path = self.audio_files[idx]

        out_file = self.embeddings_file[idx]

        with open(out_file, 'rb') as f:
            embd = pickle.load(f)

        wav,sr = torchaudio.load(wav_path)

        # take the first 3 seconds of the audio

        wav = wav[:, :3*sr]

        
        
        return wav, embd

In [12]:
def sinusoidal_positional_encoding(seq_len, hidden_dim):
    position = torch.arange(seq_len).unsqueeze(1)
    div_term = torch.exp(torch.arange(0, hidden_dim, 2) * (-torch.log(torch.tensor(10000.0)) / hidden_dim))
    pe = torch.zeros(seq_len, hidden_dim)
    pe[:, 0::2] = torch.sin(position * div_term)
    pe[:, 1::2] = torch.cos(position * div_term)
    return pe.unsqueeze(0) 

In [13]:
from speechbrain.inference.speaker import EncoderClassifier
import torch
import torch.nn as nn
import torch.nn.init as init

def reset_model_weights(model):
    """
    Reinitialize all layers in a PyTorch model with random weights 
    and ensure requires_grad is True for all parameters.
    
    Args:
        model (nn.Module): The PyTorch model to reset.
    """
    def init_weights(layer):
        """Reset weights of a given layer to random initialization."""
        if hasattr(layer, 'reset_parameters'):
            layer.reset_parameters()  # Default PyTorch reset
        elif isinstance(layer, nn.Linear):
            init.xavier_uniform_(layer.weight)
            if layer.bias is not None:
                init.zeros_(layer.bias)
        elif isinstance(layer, nn.Conv2d):
            init.kaiming_normal_(layer.weight, mode='fan_out', nonlinearity='relu')
            if layer.bias is not None:
                init.zeros_(layer.bias)
    
    # Apply the weight reset function to all layers
    model.apply(init_weights)
    
    # Ensure requires_grad is True for all parameters
    for param in model.parameters():
        param.requires_grad = True

    print("Model weights reinitialized and requires_grad set to True!")



spk_ecapa_tdnn = EncoderClassifier.from_hparams(source="speechbrain/spkrec-ecapa-voxceleb")
spk_ecapa_tdnn.device = 'cuda'

reset_model_weights(spk_ecapa_tdnn)
spk_ecapa_tdnn.mods.embedding_model.blocks[0].conv.conv.weight.requires_grad == True



/home/dcor/niskhizov/anaconda3/lib/python3.12/site-packages/speechbrain/utils/autocast.py:68: FutureWarning: `torch.cuda.amp.custom_fwd(args...)` is deprecated. Please use `torch.amp.custom_fwd(args..., device_type='cuda')` instead.
  wrapped_fwd = torch.cuda.amp.custom_fwd(fwd, cast_inputs=cast_inputs)
/home/dcor/niskhizov/anaconda3/lib/python3.12/site-packages/speechbrain/utils/checkpoints.py:200: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly 

Model weights reinitialized and requires_grad set to True!


True

In [14]:


class FusionDecoder(nn.Module):
    def __init__(self, hidden_dim, acoustic, spk_ecapa_tdnn):
        super(FusionDecoder, self).__init__()
        # self.attn = AttentionFusion(prosody_dim, hidden_dim)
        
        self.ff1 = nn.Linear(192, 512).cuda()
        self.ff2 = nn.Linear(1024, 512).cuda()

        self.base_model = copy.deepcopy(acoustic)

        self.ecapa = spk_ecapa_tdnn

    def forward(self, units, wav,  logmels):
        # units: (batch_size, time, hidden_dim)
        # emo_vecs: (batch_size, emo_vec_size)
        # spk_vecs: (batch_size, spk_vec_size)
        # logmels: (batch_size, time, n_mels)
        
        # batch_size, time, _ = units.shape
        
        # Apply attention
        o = self.base_model.encoder(units.cuda())

        emo_vecs = self.ecapa.encode_batch(wav.cuda()).squeeze(1)

        o2 = self.ff1(emo_vecs.cuda()).unsqueeze(1).expand(-1,o.shape[1] , -1)
        # units_attn = self.attn(o, emo_vecs)  # (batch_size, time, hidden_dim)

        o3 = self.ff2(torch.cat([o, o2], dim=-1))

        d = self.base_model.decoder(o3, logmels)

        return d
    
    def generate(self, units, wav):
        # units: (batch_size, time, hidden_dim)
        # emo_vecs: (batch_size, emo_vec_size)
        # spk_vecs: (batch_size, spk_vec_size)
                
        # Apply attention
        o = self.base_model.encoder(units.cuda())

        emo_vecs = self.ecapa.encode_batch(wav.cuda()).squeeze(1)

        # units_attn = self.attn(o, emo_vecs)
        o2 = self.ff1(emo_vecs.cuda()).unsqueeze(1).expand(-1,o.shape[1] , -1)
        # units_attn = self.attn(o, emo_vecs)  # (batch_size, time, hidden_dim)

        o3 = self.ff2(torch.cat([o, o2], dim=-1))


        d = self.base_model.decoder.generate(o3)
        
        return d


In [15]:
# load the latest decoder
# decoders = glob.glob('decoder_*.pth')
# decoders.sort()
# decoder.load_state_dict(torch.load(decoders[-1]))


In [16]:
ds = IemocapDataset(wav_files)

In [17]:
train_ds, test_ds = torch.utils.data.random_split(ds, [int(0.8*len(ds)), len(ds) - int(0.8*len(ds))])

In [18]:
# acoustic(units.cuda().unsqueeze(0), logmel.unsqueeze(0).transpose(1,2).cuda())

In [19]:
# acoustic.decoder(enc,logmel.unsqueeze(0).cuda().transpose(1,2))

In [20]:
ds[0][1]['logmel'].shape

torch.Size([128, 300])

In [21]:
ds[0][1]

{'discrite_units': tensor([ 6,  6,  6,  6,  6,  6, 96, 96, 96, 22, 22,  2,  2, 90, 90, 90, 56, 56,
         95, 97, 97, 20, 20,  1, 89, 89, 89, 89, 79, 79,  0,  0,  0,  0, 61, 61,
         53, 53, 10, 10, 12, 89, 89, 89, 89, 79, 79, 95, 85, 85, 85, 85, 85, 75,
         75, 75, 75, 75, 31, 31, 63, 66, 50, 50, 51, 51, 51, 20, 12, 58, 14, 59,
         13, 13,  8,  8,  0,  0,  0, 20, 33, 47, 28, 28, 86, 86, 18, 24, 17, 17,
         17, 18, 53, 53, 10, 10, 10, 13,  8,  8, 95, 98, 98, 98, 98,  9, 52, 52,
          1, 79, 31, 31, 66, 18, 18, 13, 13, 13, 84, 84, 95,  0,  0, 98, 98, 48,
         48, 48, 91, 91, 91, 91,  5,  5, 21, 21, 21, 21, 21, 45, 74, 74, 87, 45,
         87, 87, 87, 87,  6,  6]),
 'units': tensor([[ 0.2208, -0.0573, -0.3418,  ..., -0.1308, -0.3788,  0.4143],
         [ 0.2211, -0.0582, -0.3429,  ..., -0.1238, -0.3976,  0.4143],
         [ 0.2381, -0.0453, -0.3322,  ..., -0.2084, -0.3901,  0.4268],
         ...,
         [-0.0519, -0.2640, -0.7900,  ...,  0.4541, -0.7379,  0

In [22]:
# create collate function that will pad the sequences to the same length
def collate_fn(batch):
    wavs = [item[0][0] for item in batch]
    
    d_units, units, emo_vecs, spk_vecs, logmels = [], [], [], [], []
    for item in batch:
        d = item[1]['discrite_units']
        u = item[1]['units']
        mel = item[1]['logmel'].T

        d_units.append(d)
        units.append(u)
        emo_vecs.append(torch.tensor((item[1]['emo_vec'])))
        spk_vecs.append(item[1]['spk_vec'])

        mel  = mel[:u.size(0)*2,:]
        # print(mel.shape)
        mel = torch.nn.functional.pad(mel, (0,0,1,0))
        # print(mel.shape)

        logmels.append(mel)

    
    mels_lengths = torch.tensor([x.size(0) - 1 for x in logmels])
    units_lengths = torch.tensor([x.size(0) for x in units])

    d_units_padded = nn.utils.rnn.pad_sequence(d_units, batch_first=True, padding_value=-1)
    units_padded = nn.utils.rnn.pad_sequence(units, batch_first=True)
    logmels_padded = nn.utils.rnn.pad_sequence(logmels, batch_first=True)
    
    _,T,_ = units_padded.shape
    # pad the sequences

    wavs = nn.utils.rnn.pad_sequence(wavs, batch_first=True)

    
    return wavs, d_units_padded, units_padded, torch.stack(emo_vecs), torch.stack(spk_vecs), logmels_padded, mels_lengths, units_lengths

In [23]:
ds[1][1]['logmel'].shape

torch.Size([128, 300])

In [24]:
ds[0][1]['emo_vec'].shape

(1024,)

In [25]:
ds[0][1]['spk_vec'].shape

torch.Size([192])

In [26]:
train_dl = DataLoader(train_ds, batch_size=4, shuffle=True, collate_fn=collate_fn, num_workers=10)
test_dl = DataLoader(test_ds, batch_size=32, shuffle=False, collate_fn=collate_fn, num_workers=10)

In [27]:
it = iter(train_dl)

In [28]:
b= next(it)

In [29]:
wavs,d_units, units_padded, emo_vecs, spk_vecs, logmels_padded, mels_lengths, units_lengths  = b


In [30]:
acoustic = torch.hub.load("bshall/acoustic-model:main", "hubert_discrete", trust_repo=True).cuda()
decoder = FusionDecoder(512, acoustic, spk_ecapa_tdnn).cuda()


Using cache found in /home/dcor/niskhizov/cache/hub/bshall_acoustic-model_main


In [31]:
from torch.optim import Adam
from torch.nn.functional import l1_loss

optimizer = Adam(decoder.parameters(), lr=1e-6)


In [32]:
from tqdm import tqdm_notebook,tqdm

In [33]:
# torch.save(decoder.state_dict(), f"decoder_simple2_working.pth")

In [137]:
for epoch in range(3839,300000):  
    decoder.train()
    for idx,batch in tqdm(enumerate(train_dl),total=len(train_dl)):
        wavs, d_units_padded, units_padded, emo_vecs, spk_vecs, logmels_padded, mels_lengths, units_lengths  = batch
        
        optimizer.zero_grad()

        out =  decoder(d_units_padded.cuda(),wavs.cuda(),logmels_padded[:, 1:, :].cuda())
        # out = decoder(d_units_padded.cuda(), emo_vecs.cuda(), spk_vecs.cuda(), logmels_padded[:, :-1, :].cuda())
        # out = acoustic(units_padded.cuda(), logmels_padded[:, :-1, :].cuda())

        # target = hifigan(out[:1,:,:].transpose(1, 2))
        loss = l1_loss(out, logmels_padded[:, 1:, :].cuda(), reduction="none")
        loss = torch.sum(loss, dim=(1, 2)) / (out.size(-1) * mels_lengths.cuda())
        loss = torch.mean(loss)
        loss.backward()

        optimizer.step()

    if epoch % 5 == 0:
        print('Epoch:', epoch, 'Batch:', idx)
        print('Loss:', loss.item())

    if epoch % 1000 == 0:
        torch.save(decoder.state_dict(), f"decoder_simple_pretraining2_{epoch}.pth")

100%|██████████| 83/83 [00:09<00:00,  8.45it/s]

Epoch: 3840 Batch: 82
Loss: 0.3138529062271118



100%|██████████| 83/83 [00:10<00:00,  8.27it/s]


Epoch: 3845 Batch: 82
Loss: 0.32189399003982544


100%|██████████| 83/83 [00:10<00:00,  8.25it/s]

...

Epoch: 5210 Batch: 82
Loss: 0.3013620972633362



100%|██████████| 83/83 [00:12<00:00,  6.44it/s]

Epoch: 5215 Batch: 82
Loss: 0.30660557746887207



 39%|███▊      | 32/83 [00:04<00:06,  7.92it/s]


KeyboardInterrupt: 

In [136]:
epoch

3838

In [90]:
import plotly.express as px

In [91]:
px.imshow(out[0].detach().cpu().numpy().T)

## Inference

In [36]:
ls -lash --sort time | grep decoder

 80M -rw-r--r--  1 niskhizov cs_dcor  80M Feb 26 23:01 decoder_20.pth
 80M -rw-r--r--  1 niskhizov cs_dcor  80M Feb 26 22:50 decoder_10.pth
 80M -rw-r--r--  1 niskhizov cs_dcor  80M Feb 26 22:39 decoder_0.pth
 80M -rw-r--r--  1 niskhizov cs_dcor  80M Feb 26 22:18 decoder_260.pth
 80M -rw-r--r--  1 niskhizov cs_dcor  80M Feb 26 22:16 decoder_250.pth
 80M -rw-r--r--  1 niskhizov cs_dcor  80M Feb 26 22:13 decoder_240.pth
 80M -rw-r--r--  1 niskhizov cs_dcor  80M Feb 26 22:11 decoder_230.pth
 80M -rw-r--r--  1 niskhizov cs_dcor  80M Feb 26 22:08 decoder_220.pth
 80M -rw-r--r--  1 niskhizov cs_dcor  80M Feb 26 22:05 decoder_210.pth
 80M -rw-r--r--  1 niskhizov cs_dcor  80M Feb 26 22:02 decoder_200.pth
 80M -rw-r--r--  1 niskhizov cs_dcor  80M Feb 26 22:00 decoder_190.pth
 80M -rw-r--r--  1 niskhizov cs_dcor  80M Feb 26 21:57 decoder_180.pth
 80M -rw-r--r--  1 niskhizov cs_dcor  80M Feb 26 21:54 decoder_170.pth
 80M -rw-r--r--  1 niskhizov cs_dcor  80M Feb 26 21:52 decoder_160.pth
 80M -rw-r

In [158]:
emo_vecs = []
for wav_path in tqdm(wav_files):
    with torch.no_grad():
        wav,sr = torchaudio.load(wav_path)
        wav = wav[:, :]
        out = decoder.ecapa.encode_batch(wav.cuda()).squeeze(1)
        emo_vecs.append([out.cpu().detach().numpy(), wav_path])

100%|██████████| 1750/1750 [00:39<00:00, 43.85it/s]


In [159]:
emo_vecs_np = np.stack([x[0] for x in emo_vecs])

In [167]:
# do tsne analysis on the embeddings to see if they cluster 
from sklearn.manifold import TSNE
tsne = TSNE(n_components=2)

emo_vecs_tsne = tsne.fit_transform(emo_vecs_np[:,0,:])

import pandas as pd

df = pd.DataFrame(emo_vecs_tsne, columns=['x', 'y'])

df['wav'] = [x[1] for x in emo_vecs]
df['emotion'] = df['wav'].apply(lambda x: x.split('/')[-2])



px.scatter(df, x='x', y='y', hover_data=['wav'], color='emotion')





In [35]:
it = iter(test_dl)

In [36]:
batch = next(it)

In [41]:
hifigan = torch.hub.load("bshall/hifigan:main", "hifigan_hubert_discrete", trust_repo=True).cuda()

Using cache found in /home/dcor/niskhizov/cache/hub/bshall_hifigan_main
/home/dcor/niskhizov/anaconda3/lib/python3.12/site-packages/torch/nn/utils/weight_norm.py:143: FutureWarning:

`torch.nn.utils.weight_norm` is deprecated in favor of `torch.nn.utils.parametrizations.weight_norm`.



In [42]:
# with torch.no_grad():
        
#         cont_units = decoder.decoder_rnn.encoder(d_units.cuda())

#         units_attn = decoder.attn(cont_units.cuda(), emo_vecs.cuda(), spk_vecs.cuda())  # (batch_size, time, hidden_dim)
        
   
#         o = decoder.decoder_rnn.decoder.generate(units_attn)
wavs,d_units, units_padded, emo_vecs, spk_vecs, logmels_padded, mels_lengths, units_lengths  = batch

decoder = decoder.eval()

with torch.no_grad():
        

        o = decoder.generate(d_units[0].unsqueeze(0).cuda(), wavs[0].unsqueeze(0).cuda())
        

In [43]:
# acoustic = torch.hub.load("bshall/acoustic-model:main", "hubert_discrete", trust_repo=True).cuda()

# with torch.no_grad():
#     o = acoustic.generate(d_units.cuda())

In [44]:
import plotly.express as px
px.imshow(o[0].detach().cpu().numpy().T)

In [45]:
idx = 0
with torch.no_grad():
    target = hifigan(o[idx,:,:].unsqueeze(0).transpose(1, 2))

In [46]:
Audio(target[0].detach().cpu().numpy(), rate=16000)

In [47]:
Audio(wavs[22],rate=16000)

In [48]:
Audio(wavs[0],rate=16000)

In [49]:
hubert_discrete = torch.hub.load("bshall/hubert:main", "hubert_discrete", trust_repo=True).cuda()


Using cache found in /home/dcor/niskhizov/cache/hub/bshall_hubert_main


In [138]:
def extract_embedding(wav_path):
    wav, sr = torchaudio.load(wav_path)

    # take 3 seconds of audio

    with torch.inference_mode():
        # Extract speech units
        discrite_units = hubert_discrete.units(wav.unsqueeze(0).cuda())
        

    return discrite_units, wav



In [139]:
neutral_wavs = glob.glob('Emotion Speech Dataset/0018/Neutral/*.wav')

In [140]:
angry_wavs = glob.glob('Emotion Speech Dataset/0018/Angry/*.wav')

In [141]:
happy_wavs = glob.glob('Emotion Speech Dataset/0018/Happy/*.wav')

In [142]:
wav_a = "/home/dcor/niskhizov/Prosody2Vec/Emotion Speech Dataset/0018/Sad/0018_001305.wav"
wav_b ="/home/dcor/niskhizov/Prosody2Vec/Emotion Speech Dataset/0018/Angry/0018_000577.wav"#angry_wavs[10]
wav_c = happy_wavs[0]
embed_a = extract_embedding(wav_a)
embed_b = extract_embedding(wav_b)
embed_c = extract_embedding(wav_c)


In [143]:
embed_a[1].shape

torch.Size([1, 85440])

In [144]:

decoder = decoder.eval()

with torch.no_grad():
        

        o = decoder.generate(embed_a[0].unsqueeze(0).cuda(), embed_b[1].cuda())
        

In [145]:
with torch.no_grad():
    target = hifigan(o.transpose(1, 2)).cpu()[0][0]

In [146]:
Audio(target,rate = 16000)

In [147]:
Audio(embed_a[-1],rate = 16000)

In [148]:
Audio(embed_b[1],rate = 16000)

In [116]:

with torch.no_grad():
        

        o = decoder.generate(embed_b[0].unsqueeze(0).cuda(), embed_a[1].unsqueeze(0).cuda())

NotImplementedError: Only 2D, 3D, 4D, 5D padding with non-constant padding are supported for now

In [466]:
with torch.no_grad():
    target = hifigan(o.transpose(1, 2)).cpu()[0][0]

In [467]:
Audio(target,rate = 16000)


In [468]:
Audio(embed_a[-1],rate = 16000)

In [469]:
Audio(embed_b[-1],rate = 16000)